### Example

To fix ideas, consider the example from section 3.2.3 of [1]. This is an affine ODE with nondeterministic initial set and input set:

$$
    x'(t) = Ax(t) + bu(t),
$$

where:

- $x(0) \in \mathcal{X}_0 = \{(x, y) \in \mathbb{R}^2: 0.9 \leq x \leq 1.1,~~0.9 \leq y \leq 1.1\}$, and
- $u(t) \in \mathcal{U} = [-0.1, 0.1] \subset \mathbb{R}$.

The matrices $A$ and $b$ are defined below.

In [1]:
using MathematicalSystems, Reachability

using Plots
plotly()

# illustrative example (from Section 3.2.3 of Althoff's thesis)
A = 5*[-1. -4.;
        4. -1.]
n = size(A, 1)
#b = [1., 1.] # affine case
b = zeros(2)  # linear case
 
U = Interval(-0.1, 0.1)
E = Matrix{Float64}(I, 2, 2)
X0 = Hyperrectangle(low=[0.9, 0.9], high=[1.1, 1.1])
#Interval(0.9, 1.1) × Interval(0.9, 1.1)

𝒮 = ConstrainedLinearControlContinuousSystem(A, E, nothing, ConstantInput(b*U))
𝒫 = InitialValueProblem(𝒮, X0);

In [2]:
time_span = (0.0, 0.1)
T = time_span[end]

@time s = solve(𝒫, :T=>T, :δ=>0.01);
N = s.options[:N]
δ = s.options[:δ]

N, δ

 13.618579 seconds (12.91 M allocations: 684.639 MiB, 2.53% gc time)


(10, 0.01)

In [3]:
#rpipe = plot()
#plot!(rpipe, s, alpha=0.2, indices=1:N, xlabel="x₁", ylabel="x₂", label="") # solucion
plot!(rpipe, X0, color="red", alpha=0.3, xlabel="x₁", ylabel="x₂", label="") # conjunto inicial
#plot!(rpipe, s.Xk[1].X, color="green", alpha=0.1, aspectratio=1) # aprox inicial

LoadError: [91mUndefVarError: rpipe not defined[39m

In [4]:
# cannot savefig with plotly
#gr() # regenerate plot
#savefig(rpipe, "reachpipe1.png")
#plotly()

In [5]:
# UNIFORM DISTRIBUTION
# Draw some trajectories on top of the reachability computation
# distribution of the initial states
using Distributions

𝒳ₒ = Uniform(0.9, 1.1)
dt = 0.001
m = length(time_span[1]:dt:time_span[2])
NExperiments = 100
sol_all = simulate(𝒮, 𝒳ₒ, time_span, dt, NExperiments);

#traj = plot()
x_sol_all = []
y_sol_all = []
for i in 1:NExperiments
    x_sol = [Xk[1] for Xk in sol_all[i].u]
    y_sol = [Xk[2] for Xk in sol_all[i].u]
    plot!(rpipe, x_sol, y_sol, linewidth=0.5, label="", color="grey")
    push!(x_sol_all, x_sol)
    push!(y_sol_all, y_sol)
end

rpipe

LoadError: [91mUndefVarError: simulate not defined[39m

In [6]:
# now we work with a GAUSSIAN initial set
𝒳ₒ = Normal(1.0, 0.06)
dt = 0.001
m = length(time_span[1]:dt:time_span[2])
NExperiments = 100
sol_all = simulate(𝒮, 𝒳ₒ, time_span, dt, NExperiments);

#traj = plot()
x_sol_all = []
y_sol_all = []
for i in 1:NExperiments
    x_sol = [Xk[1] for Xk in sol_all[i].u]
    y_sol = [Xk[2] for Xk in sol_all[i].u]
    plot!(rpipe, x_sol, y_sol, linewidth=0.5, label="", color="grey")
    push!(x_sol_all, x_sol)
    push!(y_sol_all, y_sol)
end
rpipe

LoadError: [91mUndefVarError: simulate not defined[39m

In [7]:
σ = 0.04
𝒳ₒ = Normal(1.0, σ)
plot([Singleton(rand(𝒳ₒ, 2)) for i in 1:1000], alpha=0.3, color="grey", aspectratio=1)
plot!(X0, alpha=0.2, color="red")

In [8]:
mnormal = MvNormal([1.0, 1.0], σ^2*Matrix{Float64}(I, 2, 2))
plot([Singleton(rand(mnormal)) for i in 1:1000], alpha=0.3, color="grey", aspectratio=1)
plot!(X0, alpha=0.2, color="red")

In [9]:
pdf(mnormal, [1.0, 1.0])

99.47183943243456

In [10]:
# para graficar los conjuntos de nivel puedo mirar los puntos del plano donde la pdf tiene mas o menos el mismo valor
q = 50
muestra = linspace(0.9, 1.1, q)
X0s = Vector{Vector{Float64}}()
for xi in muestra
    for yi in muestra
        push!(X0s, [xi, yi])
    end
end
pdf.(mnormal, X0s);

In [11]:
muestra = linspace(0.9, 1.1, 200)
contour(muestra, muestra, (x,y)->Distributions.pdf(mnormal, [x,y]), aspectratio=1)

In [12]:
contour!(rpipe, muestra, muestra, (x,y)->Distributions.pdf(mnormal, [x,y]), aspectratio=1)

LoadError: [91mUndefVarError: rpipe not defined[39m

In [13]:
# Ahora lo que hacemos es separar el conjunto inicial X0 en conjuntos mas pequenos
i = 1
plot(Hyperrectangle(low=[muestra[i], muestra[i]], high=[muestra[i+1], muestra[i+1]]),alpha=0.1, aspectratio=1)
i=2
plot!(Hyperrectangle(low=[muestra[i], muestra[i]], high=[muestra[i+1], muestra[i+1]]),alpha=0.1, aspectratio=1)

In [14]:
# hecho a mano con 4 cajas
X0p = Vector{Hyperrectangle}()
push!(X0p, Hyperrectangle(low=[0.9, 0.9], high=[1.0, 1.0]))
push!(X0p, Hyperrectangle(low=[1.0, 1.0], high=[1.1, 1.1]))
push!(X0p, Hyperrectangle(low=[1.0, 0.9], high=[1.1, 1.0]))
push!(X0p, Hyperrectangle(low=[0.9, 1.0], high=[1.0, 1.1]))


plot(X0p[1], alpha=0.5, color="red")
plot!(X0p[2], alpha=0.5, color="blue")
plot!(X0p[3], alpha=0.5, color="orange")
plot!(X0p[4], alpha=0.5, color="green")
# estos serian los X0

In [15]:
rpipe2 = plot()
colors = ["red", "blue", "orange", "green"]
time_span = (0.0, 0.1)
T = time_span[end]
for (i, X0pi) in enumerate(X0p)
    𝒫 = InitialValueProblem(𝒮, X0pi)
    s = solve(𝒫, :T=>T, :δ=>0.01);
    N = s.options[:N]
    N = 1
    plot!(rpipe2, s, alpha=0.2, indices=1:N, xlabel="x₁", ylabel="x₂", label="", color=colors[i])
    plot!(rpipe2, X0pi, color="red", alpha=0.2, aspectratio=1, color=colors[i])
    #plot!(rpipe2, s.Xk[1].X, color="green", alpha=0.1, aspectratio=1)
end
rpipe2

In [16]:
# calcular el primer sucesor, X(0). veremos que estan solapados..

In [17]:
rpipe3 = plot()

i = 1
time_span = (0.0, 0.1)
T = time_span[end]
𝒫 = InitialValueProblem(𝒮, X0p[i])
s = solve(𝒫, :T=>T, :δ=>0.01);
N = s.options[:N]
N = 1
plot!(rpipe3, s, alpha=0.2, indices=1:N, xlabel="x₁", ylabel="x₂", label="", color="red", alpha=0.2)
plot!(rpipe3, X0p[i], color="red", alpha=0.2, aspectratio=1)
rpipe3

In [18]:
i = 2
time_span = (0.0, 0.1)
T = time_span[end]
𝒫 = InitialValueProblem(𝒮, X0p[i])
s = solve(𝒫, :T=>T, :δ=>0.01);
N = s.options[:N]
N = 1
plot!(rpipe3, s, alpha=0.2, indices=1:N, xlabel="x₁", ylabel="x₂", label="", color="blue", alpha=0.2)
plot!(rpipe3, X0p[i], color="blue", alpha=0.2, aspectratio=1)
rpipe3

In [19]:
# Hasta ahora estuvimos haciendo uso de reach con hiperrectangulos. Pero estaria bueno hacer reach sin
# sobreaproximacion, porque para el caso lineal no hace falta ver Apendice III
𝑋k = solve_linear(𝒫, N, T, δ);

LoadError: [91mUndefVarError: solve_linear not defined[39m

In [20]:
rpipe = plot()
plot!(rpipe, 𝑋k, alpha=0.2, xlabel="x₁", ylabel="x₂", label="") # solucion
plot!(rpipe, X0, color="red", alpha=0.5) # conjunto inicial
plot!(rpipe, 𝑋k[1], color="green", alpha=0.1, aspectratio=1) # aprox inicial

rpipe

LoadError: [91mUndefVarError: 𝑋k not defined[39m

## Interval hull of gaussian random variables

Primero considero el caso 1d.  

In [21]:
using Distributions

𝒳ₒ = Normal(1.0, 0.1) # normal con media 1.0 y varianza 0.1

nsamplesNormal = 10000
dataNormal = rand(𝒳ₒ, nsamplesNormal)
out, bin = myhist(dataNormal, 0.2, 1.8, 50)  # Compute the histogram, between -10 and 10, with 100 bins
normalised = out / (nsamplesNormal * (bin[2]-bin[1]))    # Normalised
plot(bin, normalised, markershape=:cross, markersize=2) # Plot

LoadError: [91mUndefVarError: myhist not defined[39m

In [22]:
#=
ε = Interval(-0.01, 0.01)  # conjunto pequeno que le quiero sumar a la normal
z = rand(Uniform(low(ε), high(ε)), 100)
dataShifted = []
for zi in z
    push!(dataShifted, zi + dataNormal)
    out, bin = myhist(dataShifted, 0.0, 2.0, 50)
    normalised = out / (nsamplesNormal * (bin[2]-bin[1]))
end
plot(bin, normalised, markershape=:cross, markersize=2) # Plot
r = sort(rand(𝒳ₒ, 1000))
plot([Singleton([r[i]]) for i in eachindex(r)]);
=#

In [23]:
gaussSum = plot()

N    = 80000        # Let's take N samples
data = randn(N)      # Generate N Gaussian-distributed numbers
out, bin = myhist(data, -10, 10, 100)  # Compute the histogram, between -10 and 10, with 100 bins

normalised = out / (N * (bin[2]-bin[1]))    # Normalised
plot(gaussSum, bin, normalised) # Plot

x = -10:0.1:10
y = 1./sqrt(2π) * exp.(-0.5*x.^2)

LoadError: [91mUndefVarError: myhist not defined[39m

Voy a considerar un ejemplo donde el conjunto inicial, $X_0$, es una gaussiana (1dim). La idea es construir el conjunto $\mathcal{X}(0)$ y observar su distribucion.

Si omitimos la parte de agregar el conjunto $E^+$, queda solamente hacer $CH(X_0, \Phi X_0)$.

In [24]:
𝒳ₒ = Normal(1.0, 0.1) # normal con media 1.0 y varianza 0.1


Distributions.Normal{Float64}(μ=1.0, σ=0.1)

## Appendix I: code for drawing trajectories

See affine.jl in Reachability/Trajectories module

In [25]:
using DifferentialEquations

function simulate(𝒮::AbstractSystem,
                  𝒳ₒ,                # distribution of the initial states
                  time_span,         # time span for the simulation
                  dt,                 # integration step size
                  NExperiments=100   # number of trajectories calculated
                  )

    # coefficients matrix
    #A = DiffEqArrayOperator(𝒮.A) # v0.7
    A = 𝒮.A
    f(u,p,t) = A * u
    
    # system's dimension
    n = size(A, 1)

    sol_all = []
    for i in 1:NExperiments
        x0 = rand(𝒳ₒ, n)
        # HOM = ODEProblem(DiffEqArrayOperator(A), x0, time_span) # v0.7
        HOM = ODEProblem(f, x0, time_span)
        push!(sol_all, DifferentialEquations.solve(HOM, Euler(), dt=dt))
    end

    return sol_all
end

simulate (generic function with 2 methods)

In [26]:
function plot_traj(sol_all)
    #x_t = plot()
    p = x_y = plot()
    x_sol_all = []
    y_sol_all = []
    NExperiments = length(sol_all)
    for i in 1:NExperiments
        x_sol = [Xk[1] for Xk in sol_all[i].u]
        y_sol = [Xk[2] for Xk in sol_all[i].u]
        #plot!(x_t, time, x_sol, linewidth=0.05, xaxis="time (t)", yaxis="x(t)", label="")
        p = plot!(x_y, x_sol, y_sol, linewidth=0.5, xaxis="x(t)", yaxis="y(t)", label="")

        push!(x_sol_all, x_sol)
        push!(y_sol_all, y_sol)
    end
    return p #x_sol_all, y_sol_all
end

plot_traj (generic function with 1 method)

## Appendix II: code for drawing a meshgrid

In [27]:
# see this package: https://github.com/ChrisRackauckas/VectorizedRoutines.jl/blob/master/src/matlab.jl

"""
  meshgrid(vx)
  Computes an (x,y)-grid from the vectors (vx,vx).
  For more information, see the MATLAB documentation.
  """
  meshgrid(v::AbstractVector) = meshgrid(v, v)

  """
  meshgrid(vx,vy)
  Computes an (x,y)-grid from the vectors (vx,vy).
  For more information, see the MATLAB documentation.
  """
  function meshgrid{T}(vx::AbstractVector{T}, vy::AbstractVector{T})
      m, n = length(vy), length(vx)
      vx = reshape(vx, 1, n)
      vy = reshape(vy, m, 1)
      (repmat(vx, m, 1), repmat(vy, 1, n))
end

meshgrid

In [28]:
muestra = linspace(0.9, 1.1, 4)
m = meshgrid(muestra)

([0.9 0.966667 1.03333 1.1; 0.9 0.966667 1.03333 1.1; 0.9 0.966667 1.03333 1.1; 0.9 0.966667 1.03333 1.1], [0.9 0.9 0.9 0.9; 0.966667 0.966667 0.966667 0.966667; 1.03333 1.03333 1.03333 1.03333; 1.1 1.1 1.1 1.1])

In [29]:
m[1]

4×4 Array{Float64,2}:
 0.9  0.966667  1.03333  1.1
 0.9  0.966667  1.03333  1.1
 0.9  0.966667  1.03333  1.1
 0.9  0.966667  1.03333  1.1

In [30]:
m[2]

4×4 Array{Float64,2}:
 0.9       0.9       0.9       0.9     
 0.966667  0.966667  0.966667  0.966667
 1.03333   1.03333   1.03333   1.03333 
 1.1       1.1       1.1       1.1     

## Appendix III: Reach for a linear system, error-free

In [31]:
using LazySets.Approximations
SIH = symmetric_interval_hull

𝑋i = Vector{VPolygon{Float64}}() # solutions of the discrete recurrence
Φ = expm(A * δ)
# transform the first set
Y = linear_map(Φ, X0, output_type=VPolygon) # no lo uso
P = expm(Matrix([abs.(A*δ) sparse(δ*I, n, n) spzeros(n, n);
                 spzeros(n, 2*n) sparse(δ*I, n, n);
                 spzeros(n, 3*n)]))
P2_A_δ = P[1:n, (2*n+1):3*n]
EOmegaPlus = SIH(P2_A_δ * SIH((A * A) * X0))
Ω0 = CH(X0, Φ * X0 ⊕ EOmegaPlus)

# todavia no esta soportado
#minkowski_sum(linear_map(Φ, X0), EOmegaPlus)
#

# manera rapida de convertir a poligono
𝑋0h = overapproximate(Ω0, 1e-3) # hpolygon
𝑋0 = convert(VPolygon, 𝑋0h)

LazySets.VPolygon{Float64}(Array{Float64,1}[[0.617136, 1.16251], [0.617136, 1.16251], [0.654932, 0.97606], [0.654932, 0.97606], [0.9, 0.9], [0.9, 0.9], [1.1, 0.9], [1.1, 1.1], [0.831644, 1.26644], [0.803589, 1.26644], [0.617136, 1.22864]])

In [32]:
plot(EOmegaPlus)
plot!(Φ * X0, 1e-3, alpha=0.5)
plot!(Φ * X0 ⊕ EOmegaPlus, 1e-3, alpha=0.5)
#plot!(X0, alpha=0.5)
#plot!(𝑋0, alpha=0.5)

In [33]:
expm(A)

2×2 Array{Float64,2}:
 0.00274964  -0.00615138
 0.00615138   0.00274964

In [34]:
push!(𝑋i, 𝑋0)

# calculate sets 1, ..., N-1
Φk = Φ

for k in 2:100
    𝑋k = linear_map(Φk, 𝑋0, output_type=VPolygon)
    push!(𝑋i, 𝑋k)
    Φk = Φk * Φ
end

In [35]:
plot(X0, alpha=0.5)
plot!(𝑋i[1], alpha=0.5)

In [36]:
rpipe = plot()
plot!(rpipe, 𝑋i[1], alpha=0.2, color="green")
plot!(rpipe, 𝑋i[2:10], alpha=0.2)

In [37]:
function solve_linear(𝒫, N, T, δ)
    𝑋i = Vector{VPolygon{Float64}}() # solutions of the discrete recurrence 
    A = 𝒫.s.A
    Φ = expm(A * δ)
    X0 = 𝒫.x0

    # discretize
    P = expm(Matrix([abs.(A*δ) sparse(δ*I, n, n) spzeros(n, n);
                     spzeros(n, 2*n) sparse(δ*I, n, n);
                     spzeros(n, 3*n)]))
    P2_A_δ = P[1:n, (2*n+1):3*n]
    EOmegaPlus = SIH(P2_A_δ * SIH((A * A) * X0))
    Ω0 = CH(X0, Φ * X0 ⊕ EOmegaPlus)

    # manera rapida de convertir a poligono
    𝑋0h = overapproximate(Ω0, 1e-3) # hpolygon
    𝑋0 = convert(VPolygon, 𝑋0h)
    
    push!(𝑋i, 𝑋0)

    # calculate sets 1, ..., N-1
    Φk = Φ

    for k in 2:N
        𝑋k = linear_map(Φk, 𝑋0, output_type=VPolygon)
        push!(𝑋i, 𝑋k)
        Φk = Φk * Φ
    end
    return 𝑋i
end

solve_linear (generic function with 1 method)

In [38]:
s = solve_linear(𝒫, 200, 2.0, 1.2);
s = solve_linear(𝒫, N, T, δ); # con variables en global scope

## Appendix IV: stats

https://www.reddit.com/r/Julia/comments/5l4xmx/how_to_i_compute_not_plot_a_histogram/

In [39]:
function myhist(data, min, max, nbins)
  N = length(data)             # How many elements in the input vector 'data' ?
  delta = (max-min)/nbins      # Bin size is inferred here from the maximal, minimal, and bin number
  out = zeros(nbins)           # Let's initialize the output data structures for the bin count
  bin = zeros(nbins)           # and for the bin centres...
     
  start = min                  # Left edge
  for k=1:nbins
    stop   = start + delta   # Right edge
    out[k] = length(find((data .>= start) .& (data .< stop))) # Count how many elements are between left and right 
    bin[k] = start + delta/2. # Centre of the bin
    start  = stop            # New left edge
   end
   return out, bin
end

myhist (generic function with 1 method)

In [40]:
myhist(rand(10), -1., 1., 10)

([0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 2.0, 0.0, 4.0, 2.0], [-0.9, -0.7, -0.5, -0.3, -0.1, 0.1, 0.3, 0.5, 0.7, 0.9])

In [41]:
@time myhist(rand(100), 0, 1, 100); # Precompilation

N    = 80000        # Let's take N samples
data = randn(N)      # Generate N Gaussian-distributed numbers
out, bin = myhist(data, -10, 10, 100)  # Compute the histogram, between -10 and 10, with 100 bins

x = -10:0.1:10                                  # Let me plot the theory
y = 1./sqrt(2π) * exp.(-0.5*x.^2);      # Gauss.. thank you!

normalised = out / (N * (bin[2]-bin[1]))    # Normalised
#plot(x, y)          # Plot
plot(bin, normalised) # Plot

  0.243059 seconds (151.89 k allocations: 7.993 MiB, 9.08% gc time)


## Apendice V : codigo para generar la Figura ReachPipeGaussian

(NOTA: este codigo es independiente del resto)

In [42]:
# para esto use julia v0.6.4
# requiere: solve_linear definido arriba

using MathematicalSystems, Reachability, Plots, Distributions
plotly()

rpipe = plot()

A = 5*[-1. -4.;
        4. -1.]
n = size(A, 1)
b = zeros(2)  # linear case
U = Interval(-0.1, 0.1)
E = Matrix{Float64}(I, 2, 2)
X0 = Hyperrectangle(low=[0.9, 0.9], high=[1.1, 1.1])
𝒮 = ConstrainedLinearControlContinuousSystem(A, E, nothing, ConstantInput(b*U))
𝒫 = InitialValueProblem(𝒮, X0);

N = 10
δ = 0.01
T = 1.0

Xk = solve_linear(𝒫, N, T, δ); # con variables en global scope

plot!(rpipe, Xk[1], alpha=0.3, color="green")
plot!(rpipe, Xk[2:10], alpha=0.3, color=:steelblue)
plot!(rpipe, X0, color="red", alpha=0.45, xlabel="x₁", ylabel="x₂", label="") # conjunto inicial

# now we work with a GAUSSIAN initial set
𝒳ₒ = Normal(1.0, 0.06)
dt = 0.001
m = length(time_span[1]:dt:time_span[2])
NExperiments = 100
sol_all = simulate(𝒮, 𝒳ₒ, time_span, dt, NExperiments);

#traj = plot()
x_sol_all = []
y_sol_all = []
for i in 1:NExperiments
    x_sol = [Xk[1] for Xk in sol_all[i].u]
    y_sol = [Xk[2] for Xk in sol_all[i].u]
    plot!(rpipe, x_sol, y_sol, linewidth=0.5, label="", color="grey")
    push!(x_sol_all, x_sol)
    push!(y_sol_all, y_sol)
end

rpipe